In [338]:
from xbbg import blp
import numpy as np
import math
import scipy as sp

In [339]:
bbg_tickers = 'JABAX US Equity','MSAAMMOR Index','SOFRINDX Index'
bbg_fields  = 'TOT_RETURN_INDEX_GROSS_DVDS'
bbg_start_date = '2020-06-30'
bbg_end_date = '2021-06-30'

In [340]:
df = blp.bdh(tickers=bbg_tickers, flds=bbg_fields, start_date=bbg_start_date, end_date=bbg_end_date,)
df.reset_index(level=0, inplace=True)
new_column_names = ['price_date']
new_column_names.extend(bbg_tickers)
df.columns = new_column_names
df.head()

price_date  JABAX US Equity  MSAAMMOR Index  SOFRINDX Index
0 2020-06-30            36.48        3666.084        1.041492
1 2020-07-01            36.60        3670.067        1.041495
2 2020-07-02            36.72        3692.609        1.041498
3 2020-07-03              NaN        3694.969             NaN
4 2020-07-06            37.10        3730.372        1.041511

In [341]:
df = df.dropna()
df.head()

price_date  JABAX US Equity  MSAAMMOR Index  SOFRINDX Index
0 2020-06-30            36.48       3666.0840        1.041492
1 2020-07-01            36.60       3670.0670        1.041495
2 2020-07-02            36.72       3692.6090        1.041498
4 2020-07-06            37.10       3730.3720        1.041511
5 2020-07-07            36.90       3710.3874        1.041514

In [342]:
df['previous_price'] = df[bbg_tickers[0]].shift(1)
df['price_relative'] = df[bbg_tickers[0]] / df[bbg_tickers[0]].shift(1)
df['price_return'] = np.log(df[bbg_tickers[0]] / df[bbg_tickers[0]].shift(1))

#p['num_days'] = p['price_date'].diff().dt.days 
#p.drop(index=p.index[0], axis=0, inplace=True)

cols = df.columns.to_list()
cols = cols[:2] + cols[4:] + cols[2:4]
df = df[cols]
df.head()

price_date  JABAX US Equity  previous_price  price_relative  price_return  \
0 2020-06-30            36.48             NaN             NaN           NaN   
1 2020-07-01            36.60           36.48        1.003289      0.003284   
2 2020-07-02            36.72           36.60        1.003279      0.003273   
4 2020-07-06            37.10           36.72        1.010349      0.010295   
5 2020-07-07            36.90           37.10        0.994609     -0.005405   

   MSAAMMOR Index  SOFRINDX Index  
0       3666.0840        1.041492  
1       3670.0670        1.041495  
2       3692.6090        1.041498  
4       3730.3720        1.041511  
5       3710.3874        1.041514

In [343]:
df['previous_bmk'] = df[bbg_tickers[1]].shift(1)
df['bmk_relative'] = df[bbg_tickers[1]] / df[bbg_tickers[1]].shift(1)
df['bmk_return'] = np.log(df[bbg_tickers[1]] / df[bbg_tickers[1]].shift(1))
df['active_return'] = df['price_return'] - df['bmk_return']

cols = df.columns.to_list()
cols = cols[:6] + cols[7:] + cols[6:7]
df = df[cols]
df.head()

price_date  JABAX US Equity  previous_price  price_relative  price_return  \
0 2020-06-30            36.48             NaN             NaN           NaN   
1 2020-07-01            36.60           36.48        1.003289      0.003284   
2 2020-07-02            36.72           36.60        1.003279      0.003273   
4 2020-07-06            37.10           36.72        1.010349      0.010295   
5 2020-07-07            36.90           37.10        0.994609     -0.005405   

   MSAAMMOR Index  previous_bmk  bmk_relative  bmk_return  active_return  \
0       3666.0840           NaN           NaN         NaN            NaN   
1       3670.0670      3666.084      1.001086    0.001086       0.002198   
2       3692.6090      3670.067      1.006142    0.006123      -0.002850   
4       3730.3720      3692.609      1.010227    0.010175       0.000121   
5       3710.3874      3730.372      0.994643   -0.005372      -0.000034   

   SOFRINDX Index  
0        1.041492  
1        1.041495  
2        1.041498  
4        1.041511  
5        1.041514

In [344]:
df['previous_rf'] = df[bbg_tickers[1]].shift(1)
df['rf_relative'] = df[bbg_tickers[1]] / df[bbg_tickers[1]].shift(1)
df['rf_return'] = np.log(df[bbg_tickers[1]] / df[bbg_tickers[1]].shift(1))
df['excess_return'] = df['price_return'] - df['rf_return']
df.head()

price_date  JABAX US Equity  previous_price  price_relative  price_return  \
0 2020-06-30            36.48             NaN             NaN           NaN   
1 2020-07-01            36.60           36.48        1.003289      0.003284   
2 2020-07-02            36.72           36.60        1.003279      0.003273   
4 2020-07-06            37.10           36.72        1.010349      0.010295   
5 2020-07-07            36.90           37.10        0.994609     -0.005405   

   MSAAMMOR Index  previous_bmk  bmk_relative  bmk_return  active_return  \
0       3666.0840           NaN           NaN         NaN            NaN   
1       3670.0670      3666.084      1.001086    0.001086       0.002198   
2       3692.6090      3670.067      1.006142    0.006123      -0.002850   
4       3730.3720      3692.609      1.010227    0.010175       0.000121   
5       3710.3874      3730.372      0.994643   -0.005372      -0.000034   

   SOFRINDX Index  previous_rf  rf_relative  rf_return  excess_return  
0        1.041492          NaN          NaN        NaN            NaN  
1        1.041495     3666.084     1.001086   0.001086       0.002198  
2        1.041498     3670.067     1.006142   0.006123      -0.002850  
4        1.041511     3692.609     1.010227   0.010175       0.000121  
5        1.041514     3730.372     0.994643  -0.005372      -0.000034

In [345]:
df = df.dropna()
df.head()

price_date  JABAX US Equity  previous_price  price_relative  price_return  \
1 2020-07-01            36.60           36.48        1.003289      0.003284   
2 2020-07-02            36.72           36.60        1.003279      0.003273   
4 2020-07-06            37.10           36.72        1.010349      0.010295   
5 2020-07-07            36.90           37.10        0.994609     -0.005405   
6 2020-07-08            37.08           36.90        1.004878      0.004866   

   MSAAMMOR Index  previous_bmk  bmk_relative  bmk_return  active_return  \
1       3670.0670     3666.0840      1.001086    0.001086       0.002198   
2       3692.6090     3670.0670      1.006142    0.006123      -0.002850   
4       3730.3720     3692.6090      1.010227    0.010175       0.000121   
5       3710.3874     3730.3720      0.994643   -0.005372      -0.000034   
6       3718.0110     3710.3874      1.002055    0.002053       0.002814   

   SOFRINDX Index  previous_rf  rf_relative  rf_return  excess_return  
1        1.041495    3666.0840     1.001086   0.001086       0.002198  
2        1.041498    3670.0670     1.006142   0.006123      -0.002850  
4        1.041511    3692.6090     1.010227   0.010175       0.000121  
5        1.041514    3730.3720     0.994643  -0.005372      -0.000034  
6        1.041517    3710.3874     1.002055   0.002053       0.002814

In [346]:
num_obs = len(df)
num_obs

250

In [347]:
np.mean(df['price_return']) * num_obs

0.2161012686887972

In [361]:
price_first = df['previous_price'].iloc[0]
price_last = df[bbg_tickers[0]].iloc[-1]
print(price_first, price_last, np.log(price_last / price_first))

36.48 45.28 0.216101268688797


In [349]:
sum(df['price_return'])

0.21610126868879728

In [350]:
def ret(X, n=1):
    return np.mean(X) * n
    
    
def vol(X, n=1):
    return np.std(X) * math.sqrt(n)

In [360]:
print("Rates of Return:\nprice   = %.6f\n\nbench   = %.6f\nactive  = %.6f\n\nriskless= %.6f\nexcess  = %.6f\n" % (
    ret(df['price_return'], num_obs), 
    ret(df['bmk_return'], num_obs), 
    ret(df['price_return'] - df['bmk_return'], num_obs),
    ret(df['rf_return'], num_obs), 
    ret(df['price_return'] - df['rf_return'], num_obs),
))
print("Standard Deviation:\nprice  = %.6f\nbmk  = %.6f\nactive = %.6f\n" % (
    vol(df['price_return'], num_obs), 
    vol(df['bmk_return'], num_obs), 
    vol(df['active_return'], num_obs)
))
print("Tracking Error:")

Rates of Return:
price   = 0.216101

bench   = 0.214480
active  = 0.001621

riskless= 0.214480
excess  = 0.001621

Standard Deviation:
price  = 0.099674
bmk  = 0.073933
active = 0.055716

Tracking Error:
